# Data Management – Open Data Platforms

Martin Johannes Brucker 

Student number : 942815

*Deadline:* 21.12.2023 at 23:59

In [119]:
# importing libs
import json
import folium
import ckanapi
import pandas as pd
from lxml import etree
from rdflib import Graph

# Task 1 

Select actual data sets which are public domain (“gemeinfrei”) and support linked data and are
available as RDF files. Download the newest versions of the RDF files for data processing.

In [120]:
# loading the data
# the data was downladed 01.12.2023
    
g = Graph()
g.parse("data/schulen-2023-11-01.rdf")

<Graph identifier=Nc27a446b000f49868bceb8c3792521a2 (<class 'rdflib.graph.Graph'>)>

# Task 2

Develop a Python program to demonstrate the use of RDF files by using the Python package
RDFLib. Examine the RDF file for schools (“Schulen”). Which data schema is used due to
‘schema.org’? How does the data schema look like in JSON-LD format?

In [121]:
# Query the graph to find the schema used
qres = g.query(
    """
    SELECT DISTINCT ?type
    WHERE {
        ?s a ?type .
    }
    """
)

# Print the schema used
for row in qres:
    print(f"Schema used: {row[0]}")


Schema used: http://schema.org/School
Schema used: http://schema.org/Place
Schema used: http://schema.org/GeoCoordinates
Schema used: http://schema.org/PostalAddress
Schema used: http://schema.org/Person


In [122]:
# displaying the data:
graphToJson = g.serialize(format="json-ld")
print(graphToJson)

[
  {
    "@id": "https://zufish.schleswig-holstein.de/portaldeeplink?tsa_oe_id=9117072",
    "@type": [
      "http://schema.org/School"
    ],
    "http://schema.org/address": [
      {
        "@id": "_:N024e190d901741c6aed950c558d727df"
      }
    ],
    "http://schema.org/areaServed": [
      {
        "@id": "https://zufish.schleswig-holstein.de/portaldeeplink?tsa_gebiet_id=9007260"
      }
    ],
    "http://schema.org/email": [
      {
        "@value": "Regenbogenschule.Satrup@schule.landsh.de"
      }
    ],
    "http://schema.org/employee": [
      {
        "@id": "_:Nae98910713584106ad3c9a5f668e9665"
      }
    ],
    "http://schema.org/faxNumber": [
      {
        "@value": "+49 4633 966168"
      }
    ],
    "http://schema.org/location": [
      {
        "@id": "_:Nb29eedd597c24caeaa8cafa061d97c6d"
      }
    ],
    "http://schema.org/makesOffer": [
      {
        "@id": "https://zufish.schleswig-holstein.de/portaldeeplink?tsa_leistung_id=8965507"
      },
      {

# Task 3
Examine the RDF file for police stations (“Polizeidienststellen”). Use SPARQL to query all police
stations located in “Kiel”. Provide another example query of your choice.

In [123]:
police_graph = Graph()
police_graph.parse("data/polizeidienststellen-2023-10-26.rdf", format="application/rdf+xml")

<Graph identifier=N5b8307c5bdcf4ce3b81b6dbb30e73f19 (<class 'rdflib.graph.Graph'>)>

In [124]:
# finding police stations in Kiel
query_police_stations = """
PREFIX schema: <http://schema.org/>

SELECT ?station ?name
WHERE {
  ?station a schema:PoliceStation;  # Assuming PoliceStation is the type for police stations
           schema:address ?address.
  ?address schema:addressLocality "Kiel".
  OPTIONAL { ?station schema:name ?name. }
}
"""
# Executing the query and printing the results
for row in police_graph.query(query_police_stations):
    print(f"Station URI: {row.station}, Name: {row.name if row.name else 'N/A'}")


Station URI: https://zufish.schleswig-holstein.de/portaldeeplink?tsa_oe_id=9092250, Name: 3. Polizeirevier Kiel
Station URI: https://zufish.schleswig-holstein.de/portaldeeplink?tsa_oe_id=9092804, Name: 4. Polizeirevier Kiel
Station URI: https://zufish.schleswig-holstein.de/portaldeeplink?tsa_oe_id=9093224, Name: Kriminalpolizeistelle Kiel
Station URI: https://zufish.schleswig-holstein.de/portaldeeplink?tsa_oe_id=9093825, Name: Landeskriminalamt
Station URI: https://zufish.schleswig-holstein.de/portaldeeplink?tsa_oe_id=9094379, Name: Polizei-Bezirksrevier Kiel
Station URI: https://zufish.schleswig-holstein.de/portaldeeplink?tsa_oe_id=9095329, Name: Polizeidirektion Kiel
Station URI: https://zufish.schleswig-holstein.de/portaldeeplink?tsa_oe_id=9095973, Name: Polizeistation Dietrichsdorf
Station URI: https://zufish.schleswig-holstein.de/portaldeeplink?tsa_oe_id=9096144, Name: Polizeistation Friedrichsort
Station URI: https://zufish.schleswig-holstein.de/portaldeeplink?tsa_oe_id=9096384, 

As another example in the following the latitude and longitude are extracted from the return and displayed via the folium libary

In [125]:
# Parse the XML file
root = etree.parse('data/polizeidienststellen-2023-10-26.rdf').getroot()

# Namespace dictionary
ns = {'schema': 'http://schema.org/'}

# Extract latitude and longitude values
data = []
for station in root.findall('.//schema:PoliceStation', ns):
    name = station.find('schema:name', ns).text
    latitude_element = station.find('.//schema:latitude', ns)
    longitude_element = station.find('.//schema:longitude', ns)
    
    # Skip the station if either latitude or longitude is None
    if latitude_element is None or longitude_element is None:
        continue

    latitude = latitude_element.text
    longitude = longitude_element.text
    data.append([name, latitude, longitude])

# Create a pandas DataFrame
df = pd.DataFrame(data, columns=['Name', 'Latitude', 'Longitude'])

# Convert Latitude and Longitude to float
df['Latitude'] = df['Latitude'].astype(float)
df['Longitude'] = df['Longitude'].astype(float)

# Create a map centered around the first police station
m = folium.Map(location=[df['Latitude'][0], df['Longitude'][0]], zoom_start=8)

# Add markers to the map
for _, row in df.iterrows():
    folium.Marker([row['Latitude'], row['Longitude']], popup=row['Name']).add_to(m)

# Display the map
m

# Task 4
Use the CKAN Action API endpoint of the portal “Open-Data Schleswig-Holstein”
(https://opendata.schleswig-holstein.de/api/action) to explore the organizations, packages,
groups, resources, licenses, and other data resources in a Python program. Demonstrate the
use of the CKAN Action API with examples. How can the data sets of the portal be found and
accessed via CKAN?

In [126]:
# setting up the connection to the ckan instance
ckan = ckanapi.RemoteCKAN("https://opendata.schleswig-holstein.de")


In [127]:

organisations = ckan.action.organization_list()
print(organisations)

['awsh-abfallwirtschaft-sudholstein-gmbh', 'amt-bad-oldesloe-land', 'amt-buechen', 'amt-eidertal', 'amt-elmshorn-land', 'amt-haddeby', 'amt-nortorfer-land', 'amt-schlei-ostsee', 'amt-suederbrarup', 'antikensammlung', 'bkzsh', 'bkg', 'bast', 'bundesnetzagentur', 'coworkland', 'compgen', 'delfi', 'landesmuseum-dithmarschen', 'fairtrade-deutschland', 'finanzministerium', 'fgho', 'ammersbek', 'buechen', 'stockelsdorf', 'glueckstadt', 'luebeck', 'histsem', 'klimaschutzagentur-rendsburg-eckernfoerde', 'kreis-herzogtum-lauenburg', 'nordfriesland', 'kreis-ostholstein', 'kreis-pinneberg', 'rendsburg-eckernforde', 'kreis-schleswig-flensburg', 'kreis-stormarn', 'kreisarchiv-stormarn', 'kunsthalle-kiel', 'landesamt-fur-denkmalpflege', 'llnl', 'llur', 'lfu', 'lvermgeo', 'lazuf', 'landesamt-fur-soziale-dienste', 'landesarchiv', 'lbv', 'lkn', 'landeshauptstadt-kiel', 'landesjagdverband', 'landeskriminalamt-schleswig-holstein', 'landesmeldestelle', 'mbwfk', 'mbwk', 'mekun', 'melund', 'mikws', 'milig',

In [128]:
# print the description of the organisation with the id 'landesjagdverband' 
jagdverband = ckan.action.organization_show(id='landesjagdverband')
print(jagdverband['description'])

Der Landesjagdverband Schleswig-Holstein e.V. (LJV) ist die Vereinigung der Jägerinnen und Jäger (Landesjägerschaft) und weiterer naturinteressierter Menschen Schleswig-Holsteins. Er ist ein gemeinnütziger Verein und nach dem Bundesnaturschutzgesetz (BNatSchG) staatlich anerkannter Naturschutzverein.


In [129]:
# getting the package list
packages = ckan.action.package_list()
print(packages[:5])

['01001000_bp_030_hildebrandstrasse_urschrift', '01001000_bp_033_friedrich_ebert_strasse_urschrift', '01001000_bp_034_muerwiker_strasse_1-aenderung', '01001000_bp_034_muerwiker_strasse_urschrift', '01001000_bp_035_strandfrieden_4-vereinfachte_aenderung']


In [130]:
# groups
groups = ckan.action.group_list()
print(groups)

['soci', 'educ', 'ener', 'heal', 'intr', 'just', 'agri', 'gove', 'regi', 'envi', 'tran', 'econ', 'tech']


In [131]:
ckan.action.group_show(id="tech")

{'approval_status': 'approved',
 'created': '2020-01-23T12:45:30.115416',
 'description': '',
 'display_name': 'Wissenschaft und Technologie',
 'id': 'tech',
 'image_display_url': '',
 'image_url': '',
 'is_organization': False,
 'name': 'tech',
 'num_followers': 0,
 'package_count': 685,
 'state': 'active',
 'title': 'Wissenschaft und Technologie',
 'type': 'group',
 'users': [{'about': '',
   'activity_streams_email_notifications': False,
   'capacity': 'member',
   'created': '2020-11-05T06:29:58.959287',
   'display_name': 'Admin RZ Uni Kiel',
   'email_hash': '79e5653d8d325564879d501258015ac2',
   'fullname': 'Admin RZ Uni Kiel',
   'id': '261abd51-07f1-45ad-bbc5-a9b1503c4f46',
   'image_display_url': None,
   'image_url': None,
   'last_active': '2023-12-14T10:45:59.300623',
   'name': 'adminrz',
   'number_created_packages': 0,
   'state': 'active',
   'sysadmin': True},
  {'about': '',
   'activity_streams_email_notifications': False,
   'capacity': 'member',
   'created': '202

In [132]:
# Get the packages in the group
packages = ckan.action.group_package_show(id="tech")

# Iterate over the packages to get the resources
for package in packages:
    resources = ckan.action.package_show(id=package['id'])['resources']
    for resource in resources:
        print(resource)

{'archiver': {'resource_timestamp': None, 'status_id': 0, 'is_broken': False, 'reason': '', 'url_redirected_to': 'https://opendata.schleswig-holstein.de/dataset/47bd5105-507c-4a7d-a5fd-c2659d51bc9c/resource/51ca6810-5eab-4a48-832b-a8d22775f61d/download/opendata-kfue-odl_7t.csv', 'cache_filepath': '/var/lib/ckan/default/ckan_storage/resources/51c/a68/10-5eab-4a48-832b-a8d22775f61d', 'cache_url': 'https://opendata.schleswig-holstein.de/dataset/47bd5105-507c-4a7d-a5fd-c2659d51bc9c/resource/51ca6810-5eab-4a48-832b-a8d22775f61d/download/opendata-kfue-odl_7t.csv', 'size': 158038, 'mimetype': 'text/csv', 'hash': '0e2bd275ded99976ad08acac1333d776454fa7bb', 'etag': None, 'last_modified': None, 'first_failure': None, 'last_success': '2023-12-16T07:20:07.838131', 'failure_count': 0, 'created': '2023-12-15T07:20:00.271598', 'updated': '2023-12-16T07:20:07.838131', 'status': 'Archived successfully', 'is_broken_printable': 'Downloaded OK'}, 'cache_last_updated': None, 'cache_url': None, 'created': '

In [133]:
# returning a list of available licenses
ckan.action.license_list()

[{'id': 'http://dcat-ap.de/def/licenses/ccpdm/1.0',
  'od_conformance': 'approved',
  'osd_conformance': 'not reviewed',
  'status': 'active',
  'title': 'gemeinfrei',
  'url': 'http://creativecommons.org/publicdomain/mark/1.0/'},
 {'id': 'http://dcat-ap.de/def/licenses/dl-zero-de/2.0',
  'od_conformance': 'approved',
  'osd_conformance': 'approved',
  'status': 'active',
  'title': 'Datenlizenz Deutschland – Zero – Version 2.0',
  'url': 'https://www.govdata.de/dl-de/zero-2-0'},
 {'id': 'http://dcat-ap.de/def/licenses/dl-by-de/2.0',
  'od_conformance': 'approved',
  'osd_conformance': 'not reviewed',
  'status': 'active',
  'title': 'Datenlizenz Deutschland Namensnennung 2.0',
  'url': 'https://www.govdata.de/dl-de/by-2-0'},
 {'id': 'http://dcat-ap.de/def/licenses/officialWork',
  'od_conformance': 'approved',
  'osd_conformance': 'not reviewed',
  'status': 'active',
  'title': 'Amtliches Werk, lizenzfrei nach §5 Abs. 1 UrhG',
  'url': 'http://www.gesetze-im-internet.de/urhg/__5.html

In [134]:
# getting the data for a specifig 
fireFighterStats = ckan.action.package_show(id="feuerwehreinsatze-in-kiel")
    

In [135]:
# Extract the 'extras' list
extras = fireFighterStats['extras']

# Find the dictionary in the list where the 'key' is 'spatial'
spatial_dict = next(item for item in extras if item["key"] == "spatial")

# The coordinates are stored as a string in the 'value' of the dictionary
# Parse the string into a dictionary using json.loads
spatial_value = json.loads(spatial_dict['value'])

# Extract the coordinates
coordinates = spatial_value['coordinates']

# The coordinates are stored as a list of lists
coordinates = coordinates[0]

# Swap latitude and longitude
coordinates = [[lat, lon] for lon, lat in coordinates]

In [136]:
# Create a map centered around the first set of coordinates
m = folium.Map(location=coordinates[0], zoom_start=11)

# Loop over the coordinates and add a marker for each point
for coord in coordinates:
    folium.Marker(coord).add_to(m)

# Display the map
m